In [1]:
!pip install pytorch_transformers transformers flair seqeval

     |████████████████████████████████| 184kB 2.8MB/s 
     |████████████████████████████████| 645kB 7.7MB/s 
     |████████████████████████████████| 143kB 14.0MB/s 
     |████████████████████████████████| 1.1MB 14.9MB/s 
     |████████████████████████████████| 890kB 20.0MB/s 
     |████████████████████████████████| 3.8MB 21.4MB/s 
     |████████████████████████████████| 983kB 42.5MB/s 
     |████████████████████████████████| 256kB 39.7MB/s 
     |████████████████████████████████| 798kB 40.4MB/s 
  Created wheel for seqeval: filename=seqeval-0.0.12-cp36-none-any.whl size=7424 sha256=49404dcf40d3f30d2c307ac8f0acf5485c19357abd3eb3bb7510e540da8be019
  Stored in directory: /root/.cache/pip/wheels/4f/32/0a/df3b340a82583566975377d65e724895b3fad101a3fb729f68
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893260 sha256=2fe901c25bad47d2d6c8e266613dceb54fa5281f1f99e253264acf9472743fa9
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a5012

In [2]:
import os
import csv
import sys
import torch
import logging
from flair.datasets import ColumnCorpus
from keras.preprocessing.text import text_to_word_sequence

Using TensorFlow backend.


In [0]:
from bert_sequence_tagger.model_trainer_bert import ModelTrainerBert
from bert_sequence_tagger import SequenceTaggerBert, BertForTokenClassificationCustom
from bert_sequence_tagger.bert_utils import get_model_parameters, prepare_flair_corpus
from bert_sequence_tagger.metrics import f1_entity_level, f1_token_level, f1_per_token, f1_per_token_plot
from bert_sequence_tagger.plot_classification_report import plot_classification_report
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import pandas as pd

logging.basicConfig(stream=sys.stdout, level=logging.INFO)
logger = logging.getLogger('sequence_tagger_bert')

In [4]:
os.environ['CUDA_VISIBLE_DEVICES'] = '0'

device = torch.device('cuda')
n_gpu = torch.cuda.device_count()

for i in range(n_gpu):
    print(torch.cuda.get_device_name(i))

seq_tagger = SequenceTaggerBert.load_serialized('/content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model__T047005007016_ch', BertForTokenClassificationCustom)

#locs = ['/content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model_T005','/content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model__T047005007016_check','/content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model_T016','/content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model_T047']
#models = [SequenceTaggerBert.load_serialized(x , BertForTokenClassificationCustom) for x in locs]

Tesla P100-PCIE-16GB
INFO:transformers.configuration_utils:loading configuration file /content/drive/My Drive/GITHUB/BERT/Bert_models/bert_model__T047005007016_ch/config.json
INFO:transformers.configuration_utils:Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1",
    "2": "LABEL_2",
    "3": "LABEL_3",
    "4": "LABEL_4",
    "5": "LABEL_5"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1,
    "LABEL_2": 2,
    "LABEL_3": 3,
    "LABEL_4": 4,
    "LABEL_5": 5
  },
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "output_attentions": true,
  "output_hidden_states": true,
  "pad_token_id": 0,
  "type_vocab_size": 2,
  "vocab_size": 28996
}



In [5]:
!test -d bertviz_repo && echo "FYI: bertviz_repo directory already exists, to pull latest version uncomment this line: !rm -r bertviz_repo"
# !rm -r bertviz_repo # Uncomment if you need a clean pull from repo
!test -d bertviz_repo || git clone https://github.com/jessevig/bertviz bertviz_repo
if not 'bertviz_repo' in sys.path:
  sys.path += ['bertviz_repo']

Cloning into 'bertviz_repo'...
remote: Enumerating objects: 61, done.
remote: Counting objects: 100% (61/61), done.
remote: Compressing objects: 100% (42/42), done.
remote: Total 1074 (delta 32), reused 43 (delta 19), pack-reused 1013
Receiving objects: 100% (1074/1074), 100.13 MiB | 22.34 MiB/s, done.
Resolving deltas: 100% (681/681), done.


In [0]:
from bertviz import head_view
from bertviz.neuron_view import show
from transformers import BertTokenizer, BertModel

In [0]:
def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.8/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

In [22]:
sentence_a =  "Malayan pangolins (Manis javanica) illegally imported into Guangdong province contain coronaviruses similar to SARS-CoV-2."
x = seq_tagger.predict([sentence_a.split()])[0][0]
y = ' '.join(x)
inputs = seq_tagger._bpe_tokenizer.encode_plus(sentence_a, y,return_tensors='pt', add_special_tokens=True)
token_type_ids = inputs['token_type_ids']
input_ids = inputs['input_ids']
inputs

{'input_ids': tensor([[  101, 21839,  1179, 13316, 26603,  4935,   113,  2268,  1548,   179,
         21714,  4578,   114, 19241, 11095,  1154, 23488,  3199,  4651,  1884,
         15789, 27608,  1279,  1861,  1106, 13411,  8900,   118,  3291,  2559,
           118,   123,   119,   102,   152,   152,   152,   152,   152,   152,
           152,   152,   152,   152,   157,  7629,  1571,   152,   152,   157,
          7629,  1571,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1]])}

In [24]:
print(sentence_a.split())
print(x)

['Malayan', 'pangolins', '(Manis', 'javanica)', 'illegally', 'imported', 'into', 'Guangdong', 'province', 'contain', 'coronaviruses', 'similar', 'to', 'SARS-CoV-2.']
['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'T005', 'O', 'O', 'T005']


In [0]:
input_ids = input_ids.cuda()
token_type_ids = token_type_ids.cuda()
attention = seq_tagger._bert_model(input_ids, token_type_ids=token_type_ids)[-1]

In [26]:
len(attention)

12

In [0]:
input_id_list = input_ids[0].tolist()

In [0]:
tokens = seq_tagger._bpe_tokenizer.convert_ids_to_tokens(input_id_list)

In [29]:
call_html()
head_view(attention, tokens)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [0]:
def show_head_view(model, tokenizer, text):
    inputs = tokenizer.encode_plus(text, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    input_ids = input_ids.cuda()
    attention = model(input_ids = input_ids)[-1]
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)
    call_html()
    head_view(attention, tokens)

In [19]:
text =  "coronavirus damn foa ah dawd"
show_head_view(seq_tagger._bert_model, seq_tagger._bpe_tokenizer, text)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>